# TF-IDF

TF-IDF is a method for extracting features for machine learning models from textual information.

In [1]:
from math import log

from collections import Counter
from IPython.display import HTML
import latex2mathml.converter


# set of phrases that I'll be using as the example at this page
phrases = [
    'a penny saved is a penny earned',
    'the quick brown fox jumps over the lazy dog',
    'beauty is in the eye of the beholder',
    'early to bed and early to rise makes a man healthy wealthy and wise',
    'give credit where credit is due',
    "if at first you don't succeed try try again",
    'justice delayed is justice denied',
    'keep your friends close and your enemies closer',
    'no pain no gain',
    'quickly come quickly go',
    'united we stand divided we fall',
    'when in rome do as the romans do'
]


## TF - term frequency

Term frequency is a metric for words in any next. It can be calculated using a formula:

$$tf(t,d)=\frac{n_t}{\sum_i n_i}$$

Where:

- $t$ - some word;
- $d$ - some text;
- $n_t$ - number of occurrences of word $t$ in document $d$;
- $\sum_i n_i$ - number of words in text $d$.

So in the following cell I calculate the term frequencies of the words for some phrases. The result here is a table that contains `original phrase` and `Term frequency`, which for each word from the `Original phrase` corresponds to $tf$ in the form `<word>-<tf>`.

So let's take the logic of the first phrase - "a penny saved is a penny earned" - one step at a time:

- Total count of words - $\sum_i n_i = 7$;
- You can find the word "a" twice in the phrase so - $n_{'a'} = 2 \Rightarrow tf('a')=\frac{2}{7} \approx 0.29$;
- You can find the word "penny" twice in the phrase so - $n_{'penny'}=2 \Rightarrow tf('penny')= \frac{2}{7} \approx 0.29$;
- All other words occur once so $tf$ for them can me computed as $\frac{1}{7} \approx 0.14$.

In [2]:
html_table = "<tr><th>Original phrase</th><th>Terms frequency</th></tr>"
tf_dict = {}

for p in phrases:

    words_in_phrase = dict(Counter(p.split()))
    words_count = sum(words_in_phrase.values())
    phrase_tfs = {word:number/words_count for word, number in words_in_phrase.items()}
    tf_dict[p] = phrase_tfs
    
    tf_dict
    counts_line = "<br>".join(
        [
            key + " - " + str(round(value, 2)) 
            for key, value in phrase_tfs.items()
        ]
    )
    html_table += f"<tr><td>{p}</td><td>{counts_line}</td></tr>"

HTML("<table>" + html_table + "</table>")

## IDF - inverse document frequency

For each word of a text from the given set of texts. It can be calculated using fromula:

$$idf(t,D)=log \frac{\left| D \right|}{\left| \left\{ d_i \in D | t \in d_i \right\} \right|};$$

Where:

- $D$ - set of texts;
- $\left| A \right|$ - number of elements in the set A;
- $\left| \left\{ d_i \in D | t \in d_i \right\} \right|$ - number of documents $d_i$ from set $D$ that contains word $t$;
- **Note** the denominator of the formula contains exactly the number of documents in which the word is included, not the number of occurrences of the word in any documents it's always true $\left| D \right| \geq \left| \left\{ d_i \in D | t \in d_i \right\} \right| \Rightarrow idf(t,D) \geq 0$.

So in the following cell there is an example of calculating $idf$ for a set of texts. It's displayed like a table that contains all the words from a set of texts and for each word it calculates the occurrences of the word in the set of texts and it's $idf$.

Let's take word "the" for example it occurs in 3 of 12 texts so it's $idf=log(\frac{12}{5}) \approx 1.39$.

In [4]:
phrases_number = len(phrases)
word_in_documents = Counter([w for p in phrases for w in set(p.split())])
words_idf = {}

# we need to transform directry to MathJax here.
# because quarto doesn't recognise $$ patterns in
# output cells
math_jax_expression = latex2mathml.converter.convert(
    "\left|\left\{d_i \in D | t \in d_i\\right\}\\right|"
)

html_table = (
    "<tr><th>Word</th>"
    f"<th>{math_jax_expression}</th>"
    "<th>Inverse document frequency</th></tr>"
)

for word, number in word_in_documents.items():

    idf = log(phrases_number/number)
    words_idf[word] = idf
    
    html_table += (
        f"<tr><td>{word}</td>"
        f"<td>{number}</td>"
        f"<td>{round(idf, 2)}</td></tr>"
    )

HTML("<table>" + html_table + "</table>")

This metric shows how often a word occurs in general across all texts. If the word is really common, there's a high probability that it's just an article, pretext or something like that - it doesn't make much sense in the sentence. For example, let's consider the extreme value, if you find any word $t'$ in any text, it means that $\frac{\left| D \right|}{\left| \left\{ d_i \in D | t \in d_i \right\} \right|} = 1 \Rightarrow log \frac{\left| D \right|}{\left| \left\{ d_i \in D | t \in d_i \right\} \right|} = 0$ - the presence of the word $t'$ in no way makes it possible to distinguish one entry from another.

## TF-IDF

$ft_{idf}$ is a final metric of the TF-IDF analysis and can be calculated as the product of TF and IDF. So for each word in each text from the set of texts we compute it's own value $tf_{idf}$. So in the following cell I combine results from two previous sections to compute $tf_{idf}$. For example, for word "a" in phrase "a penny saved is a penny earned" $tf_{idf} = 0.29*1.79 \approx 0.51$.

In [6]:
html_table = (
    f"""<tr>
        <th>Phrase</th>
        <th>{latex2mathml.converter.convert("tf_{idf}")}</th>
    </tr>"""
)

for phrase, tfs in tf_dict.items():
    phrase_tf_idf_line = "<br>".join([
        (
            word + " - " + 
            str(round(words_idf[word]*tf,2))
        )
        for word, tf in tfs.items()
    ])

    html_table += f"<tr><td>{phrase}</td><td>{phrase_tf_idf_line}</td></tr>"
HTML("<table>" + html_table + "</table>")       

For each record, you can perform some aggregations on the numbers received. Common aggregations are maximum and average.